In [1]:
from tensorflow.keras.models import load_model
# Define the path to the model file
model_path = r'E:\single_image_model.h5'
# Load the model with custom_objects argument
model = load_model(model_path)
# Print the model summary
#model.summary()

In [2]:
import json
import os
import tensorflow as tf
from PIL import Image
import numpy as np
from tqdm import tqdm

import os

def count_images_in_subdirs(folder_location):
    subdir_image_counts = []
    
    for subdir in os.listdir(folder_location):
        subdir_path = os.path.join(folder_location, subdir)
        
        if os.path.isdir(subdir_path):
            image_count = len([f for f in os.listdir(subdir_path) if f.lower().endswith(('.png', '.jpg', '.jpeg', '.gif', '.bmp'))])
            subdir_image_counts.append(image_count)
    
    return subdir_image_counts




img_list = []

def is_image(filename):
    try:
        with Image.open(filename) as img:
            return True
    except Exception as e:
        return False


def process_images(folder_location, target_size=(40, 40)):
    folders = os.listdir(folder_location)
    processed_images = []
    image_sizes = {}

    for folder in tqdm(folders):
        folder_path = os.path.join(folder_location, folder)
        images = os.listdir(folder_path)
        folder_image_sizes = []

        for image_name in images:
            image_path = os.path.join(folder_path, image_name)
            image = Image.open(image_path)

            # Get the original image size
            original_size = image.size
            folder_image_sizes.append(original_size)

            resized_image = tf.image.resize_with_crop_or_pad(
                tf.keras.preprocessing.image.img_to_array(image),
                target_size[0],
                target_size[1]
            )

            normalized_image = (resized_image - 127.5) / 127.5
            processed_images.append(normalized_image)
            img_list.append(image_name)

        image_sizes[folder] = folder_image_sizes

    processed_images = np.array(processed_images)
    return image_sizes, processed_images



def count_images_in_subdirs(folder_location):
    subdir_image_counts = []
    
    for subdir in os.listdir(folder_location):
        subdir_path = os.path.join(folder_location, subdir)
        
        if os.path.isdir(subdir_path):
            image_count = len([f for f in os.listdir(subdir_path) if f.lower().endswith(('.png', '.jpg', '.jpeg', '.gif', '.bmp'))])
            subdir_image_counts.append(image_count)
    
    return subdir_image_counts



def find_time(larvae):
    total_length = len(larvae)
    part_length = total_length // 3
    
    # Split the larvae array
    b = larvae[:part_length]
    m = larvae[part_length:2*part_length]
    e = larvae[2*part_length:]
    
    bb = np.mean(b, axis=0)
    mm = np.mean(m, axis=0)
    ee = np.mean(e, axis=0)
    values = [bb[1],mm[1],ee[1]]
    largest = values.index(max(values))
    return largest


def create_result_json(name, folder_location, image_sizes_dict, x, result1, count_of_ones,hc,time):
    # Convert NumPy arrays to lists
    x = x.tolist()
    y = len(result1)
    res_detailed_list = [item.tolist() for item in result1]
    result = {
        name: {
            "Subsample Name": folder_location,
            "Image Sizes": image_sizes_dict,
            "Floating Point Prediction": x,
            "Prediction": res_detailed_list,
            "Total Object Count": y,
            "Invasive Object Count": count_of_ones,
            "High COnfidence Invasive" : hc,
            "Most Likely time for Invasive" : time
        }
    }

    json_name = os.path.join(r"F:\JSONS", name + ".json")
    
    with open(json_name, 'w') as json_file:
        json.dump(result, json_file, indent=4)

import numpy as np


def model_predict_images(folder_location):
    
    image_counts = count_images_in_subdirs(folder_location)
    
    folders = folder_location.split("\\")

    folder = folders[-2]
    
    name = folder
    
    image_sizes_dict, processed_images = process_images(folder_location)

    x = model.predict(processed_images)
    
    hc_res = []
    result = []
    res_detailed = []
    time = []
    y = 0
    for i in image_counts:
        larvae = x[y:y+i]
        y = i+y
        average = np.mean(larvae, axis=0)
        pred = np.argmax(average)
        pred1 = pred
        if(pred==1):
            if(average[1]<.8):
                pred = 0
                l = find_time(larvae)
                time.append(l)
        result.append(pred1)
        hc_res.append(pred)
        res_detailed.append(average)

    count_of_ones = result.count(1)
    
    if not time:
        tn = 0
    else:
        tn = max(set(time), key = time.count)

    print("\n ------------------------ \n")

    print("Number of Total Organisms : ",len(result),"\n")
    print("Number of Invasive : ", count_of_ones,"\n")
    print("Number of High Confidence Invasive : ", hc_res.count(1),"\n")
    print("Number of Ostracod : ", result.count(2),"\n")
    print("Most likely time of veliger : ", tn,"\n")
    print("\n ------------------------ \n")

    create_result_json(name, folder_location,image_sizes_dict,x,result,count_of_ones,hc_res.count(1),tn)

In [3]:
import os

folder_location = r"D:\2.Veliger_Data\1.Samples 1 - 3\Samples 1 - 3\1 Below Lake Waco Deep 14_4 Concentrated"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

 13%|████████▋                                                         | 73/558 [01:10<06:32,  1.24it/s]


 27%|█████████████████▏                                               | 148/558 [01:53<03:55,  1.74it/s]


 40%|█████████████████████████▉                                       | 223/558 [02:40<02:11,  2.56it/s]


 53%|██████████████████████████████████▋                              | 298/558 [03:17<01:51,  2.33it/s]


 67%|███████████████████████████████████████████▌                     | 374/558 [03:50<01:16,  2.42it/s]


...

 87%|████████████████████████████████████████████████████████▊        | 684/783 [05:37<00:45,  2.19it/s]


 97%|███████████████████████████████████████████████████████████████  | 759/783 [06:16<00:13,  1.77it/s]


100%|█████████████████████████████████████████████████████████████████| 783/783 [06:28<00:00,  2.01it/s]


946/946 [==============================] - 2s 2ms/step

 ------------------------ 

Number of Total Organisms :  783 

Number of Invasive :  12 

Number of High Confidence Invasive :  0 

Number of Ostracod :  0 

Most likely time of veliger :  0 


 ------------------------ 



100%|████████████████████████████████████████████████████████████████████| 6/6 [30:19<00:00, 303.26s/it]


In [4]:
import os

folder_location = r"D:\2.Veliger_Data\1.Samples 1 - 3\Samples 1 - 3\2 Below Lake Waco Deep 28_8 Concentrated"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

 11%|███████▏                                                          | 73/671 [00:36<04:11,  2.38it/s]


 22%|██████████████▌                                                  | 150/671 [01:07<03:39,  2.37it/s]


 34%|██████████████████████                                           | 228/671 [01:43<02:19,  3.17it/s]


 45%|█████████████████████████████▎                                   | 303/671 [02:19<03:04,  2.00it/s]


 56%|████████████████████████████████████▌                            | 378/671 [02:52<02:08,  2.27it/s]


...

 86%|███████████████████████████████████████████████████████▊         | 678/789 [05:45<01:11,  1.56it/s]


 95%|██████████████████████████████████████████████████████████████   | 753/789 [06:31<00:23,  1.54it/s]


100%|█████████████████████████████████████████████████████████████████| 789/789 [06:52<00:00,  1.91it/s]


1057/1057 [==============================] - 3s 3ms/step

 ------------------------ 

Number of Total Organisms :  789 

Number of Invasive :  13 

Number of High Confidence Invasive :  4 

Number of Ostracod :  0 

Most likely time of veliger :  0 


 ------------------------ 



100%|████████████████████████████████████████████████████████████████████| 6/6 [22:50<00:00, 228.38s/it]


In [4]:
import os

folder_location = r"D:\2.Veliger_Data\1.Samples 1 - 3\Samples 1 - 3\3 Below Lake Waco Deep 14_4 Gal"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

 10%|██████▌                                                           | 82/821 [00:35<04:17,  2.88it/s]


 20%|████████████▉                                                    | 164/821 [01:09<07:00,  1.56it/s]


 30%|███████████████████▌                                             | 247/821 [01:53<05:45,  1.66it/s]


 40%|█████████████████████████▉                                       | 328/821 [02:25<01:52,  4.39it/s]


 50%|████████████████████████████████▏                                | 407/821 [03:02<03:08,  2.19it/s]


...

 92%|██████████████████████████████████████████████████████████▉     | 990/1075 [10:56<00:26,  3.27it/s]


 99%|██████████████████████████████████████████████████████████████▌| 1068/1075 [11:43<00:04,  1.51it/s]


100%|███████████████████████████████████████████████████████████████| 1075/1075 [11:47<00:00,  1.52it/s]


1223/1223 [==============================] - 4s 3ms/step

 ------------------------ 

Number of Total Organisms :  1075 

Number of Invasive :  14 

Number of High Confidence Invasive :  2 

Number of Ostracod :  0 

Most likely time of veliger :  1 


 ------------------------ 



100%|██████████████████████████████████████████████████████████████████| 6/6 [1:08:47<00:00, 687.99s/it]


In [3]:
import os

folder_location = r"D:\2.Veliger_Data\2.Samples 4 - 6\Samples 4 - 6\4_39 Below Lake Waco Shallow 100 Gal"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

  7%|████▉                                                             | 73/988 [01:16<16:16,  1.07s/it]


 15%|█████████▋                                                       | 148/988 [01:56<05:44,  2.44it/s]


 23%|███████████████▏                                                 | 230/988 [02:32<05:18,  2.38it/s]


 31%|████████████████████▎                                            | 309/988 [03:08<04:59,  2.27it/s]


 39%|█████████████████████████▎                                       | 385/988 [03:44<04:15,  2.36it/s]


...

 93%|██████████████████████████████████████████████████████████▋    | 1203/1292 [17:57<01:58,  1.33s/it]


 99%|██████████████████████████████████████████████████████████████▎| 1278/1292 [19:19<00:13,  1.03it/s]


100%|███████████████████████████████████████████████████████████████| 1292/1292 [19:32<00:00,  1.10it/s]


1599/1599 [==============================] - 5s 3ms/step

 ------------------------ 

Number of Total Organisms :  1292 

Number of Invasive :  18 

Number of High Confidence Invasive :  3 

Number of Ostracod :  0 

Most likely time of veliger :  2 


 ------------------------ 



  2%|█▌                                                               | 36/1547 [00:56<43:52,  1.74s/it]


In [4]:
import os

folder_location = r"D:\2.Veliger_Data\2.Samples 4 - 6\Samples 4 - 6\5 J H Park Surface Sample 100 Gal"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

In [ ]:
import os

folder_location = r"D:\2.Veliger_Data\May 27 2022  11-18\11 Lake Austin Reservoir"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

In [ ]:
import os

folder_location = r"D:\2.Veliger_Data\May 27 2022  11-18\12 Lake LBJ Above"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')
    


In [ ]:
import os

folder_location = r"D:\2.Veliger_Data\May 27 2022  11-18\13 Above Longhorn Dam"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

In [8]:
import os

folder_location = r"D:\2.Veliger_Data\May 27 2022  11-18\14 Above Lake Travis"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

 15%|███████████▊                                                                    | 130/879 [04:15<12:37,  1.01s/it]


 30%|███████████████████████▊                                                        | 262/879 [07:42<10:20,  1.01s/it]


 45%|███████████████████████████████████▊                                            | 394/879 [09:43<06:44,  1.20it/s]


 60%|███████████████████████████████████████████████▉                                | 527/879 [11:07<03:39,  1.60it/s]


 75%|████████████████████████████████████████████████████████████                    | 660/879 [12:33<01:29,  2.45it/s]


...

 87%|███████████████████████████████████████████████████████████████████▋          | 1326/1529 [16:42<03:48,  1.12s/it]


 95%|██████████████████████████████████████████████████████████████████████████▍   | 1458/1529 [18:23<01:09,  1.02it/s]


100%|██████████████████████████████████████████████████████████████████████████████| 1529/1529 [19:23<00:00,  1.31it/s]


2149/2149 [==============================] - 6s 3ms/step

 ------------------------ 

Number of Total Organisms :  1529 

Number of Invasive :  95 

Number of High Confidence Invasive :  22 

Number of Ostracod :  11 

Most likely time of veliger :  0 


 ------------------------ 



100%|█████████████████████████████████████████████████████████████████████████████████| 6/6 [1:02:52<00:00, 628.72s/it]


In [9]:
import os

folder_location = r"D:\2.Veliger_Data\May 27 2022  11-18\15 Below Longhorn Dam River"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

  6%|████▋                                                                          | 130/2197 [01:38<20:18,  1.70it/s]


 12%|█████████▍                                                                     | 264/2197 [03:04<30:25,  1.06it/s]


 18%|██████████████▏                                                                | 396/2197 [04:36<32:03,  1.07s/it]


 24%|███████████████████                                                            | 529/2197 [05:46<13:19,  2.09it/s]


 30%|███████████████████████▉                                                       | 665/2197 [06:54<11:31,  2.22it/s]


...

 89%|█████████████████████████████████████████████████████████████████████         | 1980/2236 [41:10<09:15,  2.17s/it]


 94%|█████████████████████████████████████████████████████████████████████████▋    | 2112/2236 [44:38<04:45,  2.30s/it]


100%|██████████████████████████████████████████████████████████████████████████████| 2236/2236 [47:34<00:00,  1.28s/it]


2995/2995 [==============================] - 9s 3ms/step

 ------------------------ 

Number of Total Organisms :  2236 

Number of Invasive :  46 

Number of High Confidence Invasive :  7 

Number of Ostracod :  1 

Most likely time of veliger :  1 


 ------------------------ 



100%|████████████████████████████████████████████████████████████████████████████████| 6/6 [3:06:15<00:00, 1862.56s/it]


In [4]:
import os

folder_location = r"D:\2.Veliger_Data\May 27 2022  11-18\16 Lake LBJ Below Dam"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

  6%|███▊                                                             | 73/1247 [00:38<09:39,  2.03it/s]


 12%|███████▉                                                        | 154/1247 [01:13<05:15,  3.47it/s]


 19%|████████████▍                                                   | 243/1247 [01:45<06:06,  2.74it/s]


 26%|████████████████▉                                               | 329/1247 [02:18<07:21,  2.08it/s]


 34%|█████████████████████▍                                          | 418/1247 [02:51<05:34,  2.48it/s]


...

 93%|██████████████████████████████████████████████████████████▍    | 1889/2036 [16:49<01:21,  1.81it/s]


 97%|█████████████████████████████████████████████████████████████▏ | 1976/2036 [17:23<00:18,  3.32it/s]


100%|███████████████████████████████████████████████████████████████| 2036/2036 [17:45<00:00,  1.91it/s]


2318/2318 [==============================] - 6s 3ms/step

 ------------------------ 

Number of Total Organisms :  2036 

Number of Invasive :  33 

Number of High Confidence Invasive :  3 

Number of Ostracod :  0 

Most likely time of veliger :  0 


 ------------------------ 



100%|██████████████████████████████████████████████████████████████████| 6/6 [1:21:07<00:00, 811.24s/it]


In [5]:
import os

folder_location = r"D:\2.Veliger_Data\May 27 2022  11-18\17 J H Park 11 Minutes"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

  7%|████▍                                                            | 73/1058 [00:45<10:23,  1.58it/s]


 14%|████████▉                                                       | 148/1058 [01:34<09:52,  1.54it/s]


 21%|█████████████▍                                                  | 223/1058 [02:24<09:16,  1.50it/s]


 28%|██████████████████                                              | 299/1058 [03:19<06:41,  1.89it/s]


 36%|██████████████████████▋                                         | 376/1058 [04:02<08:34,  1.32it/s]


...

 93%|██████████████████████████████████████████████████████████▍    | 1639/1766 [12:44<00:49,  2.57it/s]


 97%|█████████████████████████████████████████████████████████████▎ | 1717/1766 [13:14<00:20,  2.37it/s]


100%|███████████████████████████████████████████████████████████████| 1766/1766 [13:36<00:00,  2.16it/s]


1932/1932 [==============================] - 5s 2ms/step

 ------------------------ 

Number of Total Organisms :  1766 

Number of Invasive :  20 

Number of High Confidence Invasive :  2 

Number of Ostracod :  0 

Most likely time of veliger :  0 


 ------------------------ 



100%|████████████████████████████████████████████████████████████████████| 5/5 [55:31<00:00, 666.36s/it]


In [6]:
import os

folder_location = r"D:\2.Veliger_Data\May 27 2022  11-18\18 Below Tom Miller Dam"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories[5:]):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

  3%|██▏                                                              | 73/2218 [00:53<23:32,  1.52it/s]


  7%|████▍                                                           | 155/2218 [01:26<14:06,  2.44it/s]


 11%|██████▉                                                         | 239/2218 [01:57<10:33,  3.12it/s]


 14%|█████████▏                                                      | 319/2218 [02:31<13:51,  2.28it/s]


 18%|███████████▌                                                    | 399/2218 [03:06<07:19,  4.14it/s]


...

 56%|███████████████████████████████████▏                           | 1239/2218 [08:53<06:08,  2.66it/s]


 60%|█████████████████████████████████████▋                         | 1327/2218 [09:28<06:00,  2.47it/s]


 64%|████████████████████████████████████████                       | 1411/2218 [09:58<04:55,  2.73it/s]


  0%|                                                                             | 0/1 [11:09<?, ?it/s]


KeyboardInterrupt: 

In [ ]:
import os

folder_location = r"D:\2.Veliger_Data\66 Red Bud Isle Sample 18 Kayak Net 15 min_2\66 Red Bud Isle Sample 18 Kayak Net 15 min"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

In [ ]:
import os

folder_location = r"D:\2.Veliger_Data\67 Red Bud Sample 1 Kayak Net_2\67 Red Bud Sample 1 Kayak Net"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')

In [ ]:
import os

folder_location = r"D:\2.Veliger_Data\68 Red Bud Isle Sample 19 Kayak Net 13 min\68 Red Bud Isle Sample 19 Kayak Net 13 min"

# Get the list of all subdirectories
subdirectories = [f.path for f in os.scandir(folder_location) if f.is_dir()]

# Print the list of subdirectories
for subdirectory in tqdm(subdirectories):
    img_list = []
    model_predict_images(subdirectory+'\Images_001')